#### Writing to PostgreSQL

1. Insure PostgreSQL is actually installed on the system, 
2. There is a database called demo created on the said system

The cell below creates a dataframe that will be stored within postgreSQL

In [ ]:
#
# Writing to PostgreSQL database
#
import transport
from transport import providers
import pandas as pd
_data = pd.DataFrame({"name":['James Bond','Steve Rogers','Steve Nyemba'],'age':[55,150,44]})
pgw = transport.get.writer(provider=providers.POSTGRESQL,database='demo',table='friends')
pgw.write(_data,if_exists='replace') #-- default is append
print (transport.__version__)

2.0.4


#### Reading from PostgreSQL

The cell below reads the data that has been written by the cell above and computes the average age within a PostreSQL (simple query). 

- Basic read of the designated table (friends) created above
- Execute an aggregate SQL against the table


**NOTE**

By design **read** object are separated from **write** objects in order to avoid accidental writes to the database.
Read objects are created with **transport.get.reader** whereas write objects are created with **transport.get.writer**

In [ ]:

import transport
from transport import providers
pgr = transport.get.reader(provider=providers.POSTGRESQL,database='demo',table='friends')
_df = pgr.read()
_query = 'SELECT COUNT(*) _counts, AVG(age) from friends'
_sdf = pgr.read(sql=_query)
print (_df)
print ('--------- STATISTICS ------------')
print (_sdf)

           name  age
0    James Bond   55
1  Steve Rogers  150
2  Steve Nyemba   44
--------- STATISTICS ------------
   _counts   avg
0        3  83.0


An **auth-file** is a file that contains database parameters used to access the database. 
For code in shared environments, we recommend 

1. Having the **auth-file** stored on disk 
2. and the location of the file is set to an environment variable.

To generate a template of the **auth-file** open the **file generator wizard** found at visit https://healthcareio.the-phi.com/data-transport

In [ ]:
{
    "host":"klingon.io","port":5432,"username":"me","password":"foobar", "provider":"postgresql",
    "database":"demo","table":"friends"
}

{'host': 'klingon.io',
 'port': 5432,
 'username': 'me',
 'password': 'foobar',
 'provider': 'postgresql',
 'database': 'demo',
 'table': 'friends'}

#### Streaming Large Volumes of Data

It is recommended for large volumes of data to stream the data using **chunksize** as a parameter 

1. in the **read** method 
2. or **transport.get.reader(\*\*...,chunksize=1000)**

Use streaming because with large volumes of data some databases limit the volume of data for a single transaction in order to efficiently guarantee maintain **data integrity**